## For Colab only
We need to clone the repo here before we can use it

In [ ]:
!git init
!git remote add origin "https://github.com/karan-sarkar/VGGVox-PyTorch.git" 
!git pull origin master
!git branch --set-upstream-to=origin/master master

In [ ]:
!pip install -r requirements.txt

Download dataset from gdrive. The specified file is just a minimal copy of the dataset. You can upload a different file and change the ID to your file.

In [ ]:
!gdown --id '19q3G3XWKCkjwzdAWf8E-Ntx_hG-shRxo' -O data/wav.zip
!unzip ./data/wav.zip -d ./data/ && mv ./data/subset ./data/wav

In [3]:
data_dir = "./data"

## Start

In [4]:
%load_ext autoreload
%autoreload 2

In [5]:
import os
import sys
import pandas as pd
import torch
import matplotlib.pyplot as plt
%matplotlib inline
import numpy as np
sys.path.append(os.path.abspath('..'))
from train_fsl import Experiment

In [6]:
try: data_dir
except: data_dir = "/Users/pi/repos/gatech/8803-LS/Project/dataset/voxceleb2"


In [7]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(device)

cuda


In [8]:
#@title Set training params { run: "auto" }
# batch_size = 5 #@param {type:"integer"}
num_way = 5 #@param {type:"integer"}
num_shot = 5 #@param {type:"integer"}
num_epochs = 100 #@param {type:"integer"}
num_workers =  2#@param {type:"integer"}
lr = 0.00001 #@param {type:"number"}
num_train_tasks = 20 #@param {type:"integer"}
num_val_tasks = 5 #@param {type:"integer"}
num_eval_tasks = 5 #@param {type:"integer"}
augmentation = "none" #@param ["spec", "mixup", "none"]
backbone_arch = "resnet18" #@param ["resnet18", "resnet34", "audionet"]
fsl_arch = "relation-net" #@param ["relation-net", "proto-net"]

num_query =  num_shot
print('Also setting num_query to :', num_query)

Also setting num_query to : 5


In [9]:
experiment = Experiment(
    num_workers=num_workers, 
    device=device,
    num_way=num_way,
    num_shot=num_shot,
    num_query=num_query,
    num_train_tasks=num_train_tasks,
    num_val_tasks=num_val_tasks,
    num_eval_tasks=num_eval_tasks,
    num_epochs=num_epochs,
    augmentation=augmentation,
    backbone_arch=backbone_arch,
    fsl_arch=fsl_arch,
    dir=data_dir,
)

ts []
Sequential(
  (0): ExpandChannels()
  (1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
  (2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (3): ReLU(inplace=True)
  (4): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  (5): Sequential(
    (0): BasicBlock(
      (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(inplace=True)
      (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (1): BasicBlock(
      (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(in

### Explore Data

In [ ]:
loaders = experiment.Dataloaders
batch = next(iter(loaders['test']))

In [ ]:
batch[0].shape

In [ ]:
def plot_freq(dataset):
    labels = np.array(dataset.labels)
    classes, counts = np.unique(labels, return_counts=True)
    print('The number of classes is: ', len(classes))
    print('The range of samples is :', min(counts), '->', max(counts))
    classes = list(map(str, classes))
    _ = plt.bar(classes, counts)
    plt.show()
print('Train')
plot_freq(loaders['train'].dataset)
print('Val')
[plot_freq(dl.dataset) for dl in loaders['val']]
print('Test')
[plot_freq(dl.dataset) for dl in loaders['test']]

In [ ]:
train_classes = loaders['train'].dataset.labels
val_classes = loaders['val'][0].dataset.labels
test_classes = loaders['test'][0].dataset.labels
print('The 3 datasets should not have any intersection')
print('Train-Val intersection:', set(train_classes).intersection(set(val_classes)))
print('Val-Test intersection:', set(test_classes).intersection(set(val_classes)))
print('Train-Test intersection:', set(train_classes).intersection(set(test_classes)))

### Train Model

In [10]:
experiment.train()
# experiment.evaluate()

/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/connectors/callback_connector.py:91: LightningDeprecationWarning: Setting `Trainer(progress_bar_refresh_rate=3)` is deprecated in v1.5 and will be removed in v1.7. Please pass `pytorch_lightning.callbacks.progress.TQDMProgressBar` with `refresh_rate` directly to the Trainer's `callbacks` argument instead. Or, to disable the progress bar pass `enable_progress_bar = False` to the Trainer.
  f"Setting `Trainer(progress_bar_refresh_rate={progress_bar_refresh_rate})` is deprecated in v1.5 and"
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name       | Type                  | Params
-----------------------------------------------------
0 | model      | RelationNetworksMixup | 18.3 M
1 | accuracy   | Accuracy              | 0     
2 | transforms | Sequential            | 0     
-------------------------------------------

Validation sanity check: 0it [00:00, ?it/s]

/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/data_loading.py:408: UserWarning: The number of training samples (20) is smaller than the logging interval Trainer(log_every_n_steps=50). Set a lower value for log_every_n_steps if you want to see logs for the training epoch.
  f"The number of training samples ({self.num_training_batches}) is smaller than the logging interval"


Training: 0it [00:00, ?it/s]

Validating: 0it [00:00, ?it/s]

...

Validating: 0it [00:00, ?it/s]

Validating: 0it [00:00, ?it/s]

Validating: 0it [00:00, ?it/s]

The best model is stored at lightning_logs/relation-net_resnet18_none_5w_5s/version_1/checkpoints/epoch=6-step=139.ckpt


/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/trainer.py:685: UserWarning: Detected KeyboardInterrupt, attempting graceful shutdown...
  rank_zero_warn("Detected KeyboardInterrupt, attempting graceful shutdown...")


In [13]:
# multiple trainingin session in a loop
num_ways = [5]
num_shots = [5, 1]
augs = ['none', 'spec', 'mixup']
for num_way in num_ways:
    for num_shot in num_shots:
        for augmentation in augs:
            experiment = Experiment(
                num_workers=num_workers, 
                device=device,
                num_way=num_way,
                num_shot=num_shot,
                num_query=num_query,
                num_train_tasks=num_train_tasks,
                num_val_tasks=num_val_tasks,
                num_eval_tasks=num_eval_tasks,
                num_epochs=num_epochs,
                augmentation=augmentation,
                backbone_arch=backbone_arch,
                fsl_arch=fsl_arch,
                dir=data_dir,
            )
            experiment.train()


ts []
Sequential(
  (0): ExpandChannels()
  (1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
  (2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (3): ReLU(inplace=True)
  (4): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  (5): Sequential(
    (0): BasicBlock(
      (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(inplace=True)
      (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (1): BasicBlock(
      (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(in

/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/connectors/callback_connector.py:91: LightningDeprecationWarning: Setting `Trainer(progress_bar_refresh_rate=3)` is deprecated in v1.5 and will be removed in v1.7. Please pass `pytorch_lightning.callbacks.progress.TQDMProgressBar` with `refresh_rate` directly to the Trainer's `callbacks` argument instead. Or, to disable the progress bar pass `enable_progress_bar = False` to the Trainer.
  f"Setting `Trainer(progress_bar_refresh_rate={progress_bar_refresh_rate})` is deprecated in v1.5 and"
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name       | Type                  | Params
-----------------------------------------------------
0 | model      | RelationNetworksMixup | 18.3 M
1 | accuracy   | Accuracy              | 0     
2 | transforms | Sequential            | 0     
-------------------------------------------

The dataset contains very few classes: , splitting test/val/test using ratio : 0.5|0.3|0.2


Validation sanity check: 0it [00:00, ?it/s]

/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/data_loading.py:408: UserWarning: The number of training samples (20) is smaller than the logging interval Trainer(log_every_n_steps=50). Set a lower value for log_every_n_steps if you want to see logs for the training epoch.
  f"The number of training samples ({self.num_training_batches}) is smaller than the logging interval"


...

Validating: 0it [00:00, ?it/s]

Validating: 0it [00:00, ?it/s]

Validating: 0it [00:00, ?it/s]

Validating: 0it [00:00, ?it/s]

The best model is stored at lightning_logs/relation-net_resnet18_mixup_5w_1s/version_0/checkpoints/epoch=97-step=1959.ckpt


## Visualize training

In [ ]:
# Start tensorboard.
%load_ext tensorboard
%tensorboard --logdir ./lightning_logs/

In [12]:
import torch, gc
gc.collect()
torch.cuda.empty_cache()
!nvidia-smi
!sudo fuser -v /dev/nvidia*

Sun Nov 28 18:13:32 2021       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 495.44       Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla P100-PCIE...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   46C    P0    34W / 250W |   1833MiB / 16280MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [14]:
!zip -r rel_logs.zip ./lightning_logs

  adding: lightning_logs/ (stored 0%)
  adding: lightning_logs/relation-net_resnet18_spec_5w_5s/ (stored 0%)
  adding: lightning_logs/relation-net_resnet18_spec_5w_5s/version_0/ (stored 0%)
  adding: lightning_logs/relation-net_resnet18_spec_5w_5s/version_0/hparams.yaml (deflated 39%)
  adding: lightning_logs/relation-net_resnet18_spec_5w_5s/version_0/checkpoints/ (stored 0%)
  adding: lightning_logs/relation-net_resnet18_spec_5w_5s/version_0/checkpoints/last.ckpt (deflated 7%)
  adding: lightning_logs/relation-net_resnet18_spec_5w_5s/version_0/checkpoints/epoch=96-step=1939.ckpt (deflated 8%)
  adding: lightning_logs/relation-net_resnet18_spec_5w_5s/version_0/events.out.tfevents.1638124731.0bd38a99520a.306.2 (deflated 65%)
  adding: lightning_logs/relation-net_resnet18_spec_5w_1s/ (stored 0%)
  adding: lightning_logs/relation-net_resnet18_spec_5w_1s/version_0/ (stored 0%)
  adding: lightning_logs/relation-net_resnet18_spec_5w_1s/version_0/events.out.tfevents.1638129180.0bd38a99520a.30

In [15]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive
